In [49]:
import pandas as pd
import random
import json
import xlrd
import random
from math import cos, asin, sqrt, pi
import pandas as pd  

In [50]:
'''
Hacky fix. XLRD has changed a ton, open_workbook internal mechanisms deprecated on Python 3.9
''' 

xlrd.xlsx.ensure_elementtree_imported(False, None)
xlrd.xlsx.Element_has_iter = True

In [51]:
internationals = []

In [52]:
i = 1
while i < 500:
    internationals += random.sample(range(i, i+50), 5)
    i+=50
internationals += random.sample(range(i, i+10), 1)

In [53]:
len(internationals)

51

In [54]:
print(*internationals)

14 39 20 36 13 75 72 67 58 60 122 149 137 115 138 164 185 154 177 183 217 245 210 236 209 254 272 290 271 285 338 342 301 348 309 389 367 357 360 362 432 438 414 429 445 468 465 489 457 485 507


In [55]:
with open('int_locations.txt') as f:
    intl_locations = f.read().splitlines()

In [56]:
intl = dict(zip(internationals, intl_locations))

In [57]:
years_in_future = 2
age_tid = [(-2, 18), (-4, 17), (-5, 16)]
#age_tid = [(-2, 18), (-2, 17), (-4, 16), (-5, 15)]

In [58]:
age = age_tid[years_in_future][1]
diff = age-18
tid = age_tid[years_in_future][0]

In [59]:
def getJSON(filePath):    
    with open(filePath, encoding='utf-8-sig') as fp:
        return json.load(fp)


In [60]:
def writeJSON(filePath, obj):
    with open(filePath, 'r+',encoding='utf-8') as fp:
        json.dump(obj, fp, indent=4)

In [61]:
def getName(country):
    if country in main_names["gameAttributes"]["playerBioInfo"]["countries"]:
        names = main_names["gameAttributes"]["playerBioInfo"]["countries"][country]
    elif country in other_names["gameAttributes"]["playerBioInfo"]["countries"]:
        names = other_names["gameAttributes"]["playerBioInfo"]["countries"][country]
    else:
        return None
    return (random.choice(list(names["first"].keys())[1:]), random.choice(list(names["last"].keys())[1:]))

In [62]:
fileName = '2069 Post-CT.json'
obj = getJSON(fileName)
year = int(obj.get("meta")["phaseText"][0:4]) 
main_names = getJSON("playerBioInfo_6.json")
other_names = getJSON("playerBioInfo_2.json")

In [63]:
cols = ['Name','Hgt', 'Ovr']
class_df = pd.DataFrame(columns = cols)

In [64]:
i = 0
print(age)
print(year)
print(tid)
for player in obj.get("players"):
    ratings = player["ratings"][-1]
    if ratings["season"] == year - diff and player["tid"] == tid and year - player.get("born")["year"] == age:
        name = player["firstName"] + " " + player["lastName"]
        class_df.loc[i, "Name"] = name
        class_df.loc[i, "Ovr"] = ratings['ovr']
        class_df.loc[i, "Hgt"] = ratings["hgt"]
        i+=1
class_df = class_df.sort_values(by=['Ovr'], ascending = False)
class_df = class_df.reset_index(drop=True)

16
2069
-5


In [65]:
def getType(hgt):
    randType = random.random()

    if (hgt >= 59):

        if (randType < 0.02):
            type = "captain"
        elif (randType < 0.09):
            type = "triple dub"
        elif (randType < 0.20):
            type = "fundamentals"
        elif (randType < 0.35):
            type = "athletic big"
        elif (randType < 0.55):
            type = "offensive big"
        elif (randType < 0.75):
            type = "stretch big"
        elif (randType < 0.95):
            type = "defensive big"
        else:
            type = "unicorn"
    elif (hgt <= 36):
        #6'3" or shorter
        if (randType < 0.03):
            type = "captain"
        elif (randType < 0.08):
            type = "triple dub"
        elif (randType < 0.20):
            type = "athletic guard"
        elif (randType < 0.32):
            type = "3_and_d"
        elif (randType < 0.42):
            type = "defense only"
        elif (randType < 0.50):
            type = "jhart"
        elif (randType < 0.60):
            type = "fundamentals"
        elif (randType < 0.65):
            type = "rondo"
        elif (randType < 0.78):
            type = "shooter"
        elif (randType < 0.90):
            type = "slasher"
        else:
            type = "pure point"
    else:
        if (randType < 0.03):
            type = "captain"
        elif (randType < 0.12):
            type = "3_and_d"
        elif (randType < 0.23):
            type = "athletic big"
        elif (randType < 0.33):
            type = "athletic guard"
        elif (randType < 0.43):
            type = "defense only"
        elif (randType < 0.53):
            type = "fundamentals"
        elif (randType < 0.63):
            type = "shooter"
        elif (randType < 0.72):
            type = "slasher"
        elif (randType < 0.80):
            type = "triple dub"
        elif (randType < 0.90):
            type = "derozan"
        else:
            type = "versatile"
    return type



In [66]:
def getBaselineAdj(row):
    ratingsAdjustment = random.randint(-15, 15)
    return ratingsAdjustment


def bound(low, high, value):
    return max(low, min(high, value))


def getFactor(row):
    factor = bound(0.2, 1.2, random.gauss(1., 0.2))
    return factor

def getFuzz(value):
    factor = random.gauss(value, 3)
    return factor


def getPretty(value):
    final = round(bound(0.,100.,value))
    return final

def getComposite(ratings, weights):
    num = 0
    denom = 0
    for r, w in zip(ratings, weights):
        num += w * r
        denom += 100 * w
    return num/denom

def calcPos(ratings):
    position = ""
    if ratings["hgt"] >= 59:
        position = "C"
    elif ratings["hgt"] >= 52:
        position = "PF"
    elif ratings["hgt"] >= 44:
        position = "SF"
    elif ratings["hgt"] >= 30:
        position = "SG"
    else:
        position = "G"
        
    pg = sg = sf = pf = c = False
    if (ratings["spd"] >= 60 and ratings["pss"] >= 50 and ratings["drb"] >= 50) or (ratings["spd"] >= 40 and ratings["pss"] >= 65 and ratings["drb"] >= 65):
        pg = True
    if ratings["spd"] >= 50 and ratings["drb"] >= 50 and ratings["hgt"] >= 30 and (ratings["dnk"] >= 58 or ratings["tp"] > 63):
        sg = True
    if ratings["spd"] >= 40 and ratings["drb"] >= 30 and ratings["hgt"] >= 44 and (ratings["dnk"] >= 58 or ratings["tp"] > 63):
        sg = True
    if ratings["hgt"] >= 44 and ratings["stre"] >= 55 and (ratings["hgt"] + ratings["stre"] >= 110) and (ratings["hgt"] <= 63 or ratings["tp"] > 60):
        pf = True
    if ratings["hgt"] >= 63 or (ratings["hgt"] >= 54 and ratings["stre"] >= 75):
        c = True
        pg = False
        sg = False
    
    if pg and not sg and not sf and not pf and not c:
        position = "PG"
    elif not pg and sg and not sf and not pf and not c:
        position = "SG"
    elif not pg and not sg and sf and not pf and not c:
        position = "SF"
    elif not pg and not sg and not sf and  pf and not c:
        position = "PF"
    elif not pg and not sg and not sf and not pf and  c:
        position = "C"
    
    if c and (pg or sg):
        position = "F"
    elif (pg or sg) and (sf or pf):
        position = "GF"
    elif c and (pf or sf):
        position = "FC"
    elif pf and sf:
        position = "F"
    elif pg and sg:
        position = "G"

    return position
        
    
def getAtts(type):
    cutoff = 0.61
    if type == '3':
        ratings = ['Oiq', 'Tp']
        weights = [0.1, 1]
        cutoff = 0.59
    if type == 'A':
        ratings = ["Stre", "Spd", "Jmp", "Hgt"]
        weights = [1, 1, 1, 0.75]
        cutoff = 0.63
    if type == 'B':
        ratings = ['Drb', 'Spd']
        weights = [1, 1]
        cutoff = 0.68
    if type == 'Di':
        ratings = ["Hgt", "Stre", "Spd", "Jmp", "Diq"]
        weights = [2.5, 1, 0.5, 0.5, 2]
        cutoff = 0.57
    if type == 'Dp':
        ratings = ["Hgt", "Stre", "Spd", "Jmp", "Diq"]
        weights = [0.5, 0.5, 2, 0.5, 1]
    if type == 'Po':
        ratings = ["Hgt", "Stre", "Spd", "Ins", "Oiq"]
        weights = [2, 0.6, 0.2, 1, 0.2]
    if type == 'Ps':
        ratings = ["Drb", "Pss", "Oiq"]
        weights = [0.1, 1]
        cutoff = 0.63
    if type == 'R':
        ratings = ["Hgt", "Stre", "Jmp", "Reb", "Oiq", "Diq"]
        weights = [2, 0.1, 0.1, 2, 0.5, 0.5]
    return (ratings, weights, cutoff)

def getTypeFactor(rating, playerType, ratingName):
    value_returned = rating
    if playerType == 'pure point':
        if ratingName == 'Drb':
            value_returned = 1.4 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.2 * rating
        elif ratingName == 'Spd':
            value_returned = 1.4 * rating
        elif ratingName == 'Ins':
            value_returned = 1.5 * rating
        elif ratingName == 'Pss':
            value_returned = 1.6 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.5 * rating
        elif ratingName == 'Reb':
            value_returned = 0.8 * rating
        elif ratingName == 'Diq':
            value_returned = 1.2 * rating
        elif ratingName == 'Tp':
            value_returned = 1.2 * rating
    elif playerType == 'rondo':
        if ratingName == 'Drb':
            value_returned = 1.4 * rating
        elif ratingName == 'Stre':
            value_returned = 0.7 * rating
        elif ratingName == 'Reb':
            value_returned = 0.8 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.2 * rating
        elif ratingName == 'Spd':
            value_returned = 1.45 * rating
        elif ratingName == 'Ins':
            value_returned = 1.4 * rating
        elif ratingName == 'Pss':
            value_returned = 1.7 * rating
        elif ratingName == 'Ft':
            value_returned = 0.9 * rating
        elif ratingName == 'Fg':
            value_returned = 0.7 * rating
        elif ratingName == 'Tp':
            value_returned = 0.7 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.8 * rating
        elif ratingName == 'Diq':
            value_returned = 1.2 * rating
    elif playerType == 'athletic guard':
        if ratingName == 'Jmp':
            value_returned = 1.6 * rating
        elif ratingName == 'Spd':
            value_returned = 1.6 * rating
        elif ratingName == 'Stre':
            value_returned = 1.3 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.5 * rating
        elif ratingName == 'Ins':
            value_returned = 1.4 * rating
        elif ratingName == 'Oiq':
            value_returned = 0.8 * rating
        elif ratingName == 'Endu':
            value_returned = 1.45 * rating
        elif ratingName == 'Pss':
            value_returned = 0.9 * rating
        elif ratingName == 'Drb':
            value_returned = 1.2 * rating
    elif playerType == 'triple dub':
        if ratingName == 'Jmp':
            value_returned = 1.3 * rating
        elif ratingName == 'Stre':
            value_returned = 1.2 * rating
        elif ratingName == 'Spd':
            value_returned = 1.15 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.2 * rating
        elif ratingName == 'Ins':
            value_returned = 1.25 * rating
        elif ratingName == 'Pss':
            value_returned = 1.35 * rating
        elif ratingName == 'Reb':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 1.2 * rating
    elif playerType == '3_and_d':
        if ratingName == 'Jmp':
            value_returned = 1.3 * rating
        elif ratingName == 'Spd':
            value_returned = 1.3 * rating
        elif ratingName == 'Stre':
            value_returned = 1.2 * rating
        elif ratingName == 'Drb':
            value_returned = 0.8 * rating
        elif ratingName == 'Pss':
            value_returned = 0.7 * rating
        elif ratingName == 'Ft':
            value_returned = 1.3 * rating
        elif ratingName == 'Fg':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 1.4 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.25 * rating
        elif ratingName == 'Diq':
            value_returned = 1.1 * rating
        elif ratingName == 'Endu':
            value_returned = 1.15 * rating
    elif playerType == 'captain':
        if ratingName == 'Jmp':
            value_returned = 1.3 * rating
        elif ratingName == 'Drb':
            value_returned = 1.2 * rating
        elif ratingName == 'Pss':
            value_returned = 1.2 * rating
        elif ratingName == 'Stre':
            value_returned = 1.2 * rating
        elif ratingName == 'Spd':
            value_returned = 1.35 * rating
        elif ratingName == 'Ins':
            value_returned = 1.3 * rating
        elif ratingName == 'Reb':
            value_returned = 1.2 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.2 * rating
        elif ratingName == 'Ft':
            value_returned = 1.2 * rating
        elif ratingName == 'Fg':
            value_returned = 1.2 * rating
        elif ratingName == 'Tp':
            value_returned = 1.3 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.6 * rating
        elif ratingName == 'Diq':
            value_returned = 1.6 * rating
        elif ratingName == 'Endu':
            value_returned = 1.5 * rating
    elif playerType == 'fundamentals':
        if ratingName == 'Jmp':
            value_returned = 0.75 * rating
        elif ratingName == 'Spd':
            value_returned = 0.75 * rating
        elif ratingName == 'Drb':
            value_returned = 1.3 * rating
        elif ratingName == 'Pss':
            value_returned = 1.35 * rating
        elif ratingName == 'Ft':
            value_returned = 1.5 * rating
        elif ratingName == 'Ins':
            value_returned = 1.4 * rating
        elif ratingName == 'Fg':
            value_returned = 1.2 * rating
        elif ratingName == 'Tp':
            value_returned = 1.1 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.2 * rating
        elif ratingName == 'Diq':
            value_returned = 1.2 * rating
        elif ratingName == 'Reb':
            value_returned = 1.2 * rating
        elif ratingName == 'Endu':
            value_returned = 0.7 * rating
    elif playerType == 'defensive big':
        if ratingName == 'Stre':
            value_returned = 1.25 * rating
        elif ratingName == 'Reb':
            value_returned = 1.6 * rating
        elif ratingName == 'Ft':
            value_returned = 0.8 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.35 * rating
        elif ratingName == 'Ins':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 0.6 * rating
        elif ratingName == 'Drb':
            value_returned = 0.6 * rating
        elif ratingName == 'Pss':
            value_returned = 0.7 * rating
        elif ratingName == 'Diq':
            value_returned = 1.55 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.3 * rating
    elif playerType == 'offensive big':
        if ratingName == 'Stre':
            value_returned = 1.4 * rating
        elif ratingName == 'Reb':
            value_returned = 1.4 * rating
        elif ratingName == 'Spd':
            value_returned = 0.9 * rating
        elif ratingName == 'Ins':
            value_returned = 1.5 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.5 * rating
        elif ratingName == 'Tp':
            value_returned = 0.8 * rating
        elif ratingName == 'Fg':
            value_returned = 1.1 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.2 * rating
        elif ratingName == 'Diq':
            value_returned = 0.9 * rating
    elif playerType == 'athletic big':
        if ratingName == 'Stre':
            value_returned = 1.35 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.55 * rating
        elif ratingName == 'Ins':
            value_returned = 1.4 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.4 * rating
        elif ratingName == 'Reb':
            value_returned = 1.4 * rating
        elif ratingName == 'Ft':
            value_returned = 0.7 * rating
        elif ratingName == 'Fg':
            value_returned = 0.9 * rating
        elif ratingName == 'Tp':
            value_returned = 0.75 * rating
        elif ratingName == 'Oiq':
            value_returned = 0.75 * rating
        elif ratingName == 'Diq':
            value_returned = 0.75 * rating
        elif ratingName == 'Endu':
            value_returned = 1.4 * rating
    elif playerType == 'stretch big':
        if ratingName == 'Stre':
            value_returned = 1.1 * rating
        elif ratingName == 'Reb':
            value_returned = 0.7 * rating
        elif ratingName == 'Drb':
            value_returned = 0.8 * rating
        elif ratingName == 'Pss':
            value_returned = 0.8 * rating
        elif ratingName == 'Ft':
            value_returned = 1.25 * rating
        elif ratingName == 'Fg':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 1.4 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.3 * rating
        elif ratingName == 'Diq':
            value_returned = 0.9 * rating
    elif playerType == 'unicorn':
        if ratingName == 'Dnk':
            value_returned = 0.7 * rating
        if ratingName == 'Endu':
            value_returned = 0.7 * rating
        elif ratingName == 'Stre':
            value_returned = 0.6 * rating
        elif ratingName == 'Reb':
            value_returned = 0.8 * rating
        elif ratingName == 'Pss':
            value_returned = 1.4 * rating
        elif ratingName == 'Ft':
            value_returned = 1.5 * rating
        elif ratingName == 'Fg':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 1.35 * rating
        elif ratingName == 'Spd':
            value_returned = 0.65 * rating
        elif ratingName == 'Diq':
            value_returned = 0.9 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.2 * rating
    elif playerType == 'defense only':
        if ratingName == 'Stre':
            value_returned = 1.3 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.5 * rating
        elif ratingName == 'Spd':
            value_returned = 1.4 * rating
        elif ratingName == 'Reb':
            value_returned = 1.4 * rating
        elif ratingName == 'Ft':
            value_returned = 0.6 * rating
        elif ratingName == 'Ins':
            value_returned = 1.2 * rating
        elif ratingName == 'Fg':
            value_returned = 0.6 * rating
        elif ratingName == 'Tp':
            value_returned = 0.6 * rating
        elif ratingName == 'Drb':
            value_returned = 0.8 * rating
        elif ratingName == 'Diq':
            value_returned = 1.65 * rating
        elif ratingName == 'End':
            value_returned = 1.3 * rating
    elif playerType == 'jhart':
        if ratingName == 'Stre':
            value_returned = 1.25 * rating
        elif ratingName == 'Reb':
            value_returned = 1.2 * rating
        elif ratingName == 'Endu':
            value_returned = 1.3 * rating
        elif ratingName == 'Ft':
            value_returned = 0.8 * rating
        elif ratingName == 'Fg':
            value_returned = 0.8 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.2 * rating
        elif ratingName == 'Ins':
            value_returned = 1.1 * rating
        elif ratingName == 'Tp':
            value_returned = 1.1 * rating
        elif ratingName == 'Drb':
            value_returned = 0.8 * rating
        elif ratingName == 'Pss':
            value_returned = 1.1 * rating
        elif ratingName == 'Diq':
            value_returned = 1.3 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.3 * rating
    elif playerType == 'shooter':
        if ratingName == 'Stre':
            value_returned = 0.8 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.1 * rating
        elif ratingName == 'Spd':
            value_returned = 1.1 * rating
        elif ratingName == 'Reb':
            value_returned = 0.8 * rating
        elif ratingName == 'Ft':
            value_returned = 1.6 * rating
        elif ratingName == 'Fg':
            value_returned = 1.55 * rating
        elif ratingName == 'Tp':
            value_returned = 1.5 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.4 * rating
        elif ratingName == 'Pss':
            value_returned = 0.9 * rating
        elif ratingName == 'Diq':
            value_returned = 0.95 * rating
    elif playerType == 'slasher':
        if ratingName == 'Dnk':
            value_returned = 1.5 * rating
        elif ratingName == 'Ins':
            value_returned = 1.4 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.35 * rating
        elif ratingName == 'Spd':
            value_returned = 1.35 * rating
        elif ratingName == 'Fg':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 0.95 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.3 * rating
        elif ratingName == 'Drb':
            value_returned = 1.2 * rating
        elif ratingName == 'Pss':
            value_returned = 0.9 * rating
    elif playerType == 'derozan':  
        if ratingName == 'Ft':
            value_returned = 1.5 * rating
        elif ratingName == 'Fg':
            value_returned = 1.6 * rating
        elif ratingName == 'Tp':
            value_returned = 0.5 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.5 * rating
        elif ratingName == 'Drb':
            value_returned = 1.3 * rating
    elif playerType == 'versatile':
        if ratingName == 'Drb':
            value_returned = 1.2 * rating
        elif ratingName == 'Pss':
            value_returned = 1.1 * rating
        elif ratingName == 'Dnk':
            value_returned = 1.35 * rating
        elif ratingName == 'Jmp':
            value_returned = 1.35 * rating
        elif ratingName == 'Spd':
            value_returned = 1.35 * rating
        elif ratingName == 'Ft':
            value_returned = 1.3 * rating
        elif ratingName == 'Fg':
            value_returned = 1.3 * rating
        elif ratingName == 'Tp':
            value_returned = 1.2 * rating
        elif ratingName == 'Reb':
            value_returned = 1.3 * rating
        elif ratingName == 'Oiq':
            value_returned = 1.3 * rating
        elif ratingName == 'Diq':
            value_returned = 1.25 * rating
    return value_returned



In [67]:
def getOvr(value):
    if value >= 68.:
        return round(value+8.)
    elif value >= 50.:
        return round(value+ (4. + ((value - 50.) * (4. / 18.))))
    elif value >= 42.:
        return round(value+ (-5. + (value -42.) * (10. / 8.)))
    elif value >= 31.:
        return round(value+ (-5. - (42.-value) * (5. / 11.) ))
    else:
        return round(value -10.)
   

In [68]:
def generate_class():
    ratings_list = ['Stre','Spd','Jmp','Endu','Ins','Dnk','Ft','Fg','Tp','Oiq','Diq','Drb','Pss','Reb']
    athl_list = ['Stre','Spd','Jmp','Endu','Dnk']
    shoot_list = ['Ft','Fg','Tp']
    skill_list = ['Oiq','Drb','Pss']

    class_df['Hgt'] = class_df['Hgt'].astype(int)


    class_df['ratingsAdjustment'] = class_df.apply(getBaselineAdj, axis=1)

    class_df['factorAthleticism'] = class_df.apply(getFactor, axis=1)
    class_df['factorShooting'] = class_df.apply(getFactor, axis=1)
    class_df['factorSkill'] = class_df.apply(getFactor, axis=1)
    class_df['factorD'] = class_df.apply(getFactor, axis=1)
    class_df['factorReb'] = class_df.apply(getFactor, axis=1)

    class_df['playerType'] = class_df.apply(lambda x: getType(x['Hgt']), axis=1)

    class_df['Stre'] = 37 + class_df['ratingsAdjustment']
    class_df['Spd'] = 40 + class_df['ratingsAdjustment']
    class_df['Jmp'] = 40 + class_df['ratingsAdjustment']
    class_df['Endu'] = 17 + class_df['ratingsAdjustment']
    class_df['Ins'] = 27 + class_df['ratingsAdjustment']
    class_df['Dnk'] = 27 + class_df['ratingsAdjustment']
    class_df['Ft'] = 32 + class_df['ratingsAdjustment']
    class_df['Fg'] = 32 + class_df['ratingsAdjustment']
    class_df['Tp'] = 32 + class_df['ratingsAdjustment']
    class_df['Oiq'] = 22 + class_df['ratingsAdjustment']
    class_df['Diq'] = 22 + class_df['ratingsAdjustment']
    class_df['Drb'] = 37 + class_df['ratingsAdjustment']
    class_df['Pss'] = 37 + class_df['ratingsAdjustment']
    class_df['Reb'] = 37 + class_df['ratingsAdjustment']
    for rating in ratings_list:
        class_df[rating] = class_df.apply(lambda x: getFuzz(x[rating]), axis=1)

    for ath_rating in athl_list:
        class_df[ath_rating] = class_df[ath_rating] * class_df['factorAthleticism']

    for shoot_rating in shoot_list:
        class_df[shoot_rating] = class_df[shoot_rating] * class_df['factorShooting']

    for skill_rating in skill_list:
        class_df[skill_rating] = class_df[skill_rating] * class_df['factorSkill']

    class_df['Diq'] = class_df['Diq'] * class_df['factorD']
    class_df['Reb'] = class_df['Reb'] * class_df['factorReb']

    for rating in ratings_list:
        class_df[rating] = class_df.apply(lambda x: getTypeFactor(x[rating], x['playerType'], rating), axis=1)
    
    for rating in ratings_list:
        class_df[rating] = class_df.apply(lambda x: getPretty(x[rating]), axis=1)

    class_final = class_df[['Name','playerType','Hgt','Stre','Spd','Jmp','Endu','Ins','Dnk','Ft','Fg','Tp','Oiq','Diq','Drb','Pss','Reb']]
    class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
    
    class_final['Ovr'] = class_final.apply(lambda x: getOvr(x['Ovr_stp1']), axis=1)
    
    class_final['Hometown'] = ''
    class_final['HS'] = ''
        
    class_final = class_final.sort_values('Ovr', ascending=False).reset_index()

    class_final = class_final[['Name','playerType','Ovr', 'Ovr_stp1','Hgt','Stre','Spd','Jmp','Endu','Ins','Dnk','Ft','Fg','Tp','Oiq','Diq','Drb','Pss','Reb', 'Hometown', 'HS']]
    
    return class_final

In [69]:
class_average_top_5 = 0.
counter = 0
class_variance_top_5 = 9999.
while (True):
    counter+=1
    class_done = generate_class()
    class_average_top_5 =  class_done['Ovr'].head(5).mean(axis=0)
    class_variance_top_5 =  class_done['Ovr'].head(5).var(axis=0)
    
    five_star_end = class_done.loc[29,'Ovr']
    rec50 = class_done.loc[49,'Ovr']
    four_star_end = class_done.loc[149,'Ovr']
    
    three_star_end = class_done.loc[249,'Ovr']
    if(class_done['Hgt'].head(8).max() >= 62):
        if ((class_average_top_5 >= 68.0) & (class_average_top_5 <= 71.)):
            if class_variance_top_5 <=10.:
                if (five_star_end  <= 56.) & (five_star_end >= 52.):
                    if (four_star_end  <= 38.) & (four_star_end >= 34.):
                        if (three_star_end  <= 30.) & (three_star_end >= 26.):
                            if (rec50 <= 50.) & (rec50 >= 46):
                                print(counter)
                                break
                            else:
                                print("Recruit 50 not in bounds")
                        else:
                            print("3 star end not in bounds")
                    else:
                        print("4 star end not in bounds")
                else:
                    print("5 star end not in bounds")
            else:
                print("Top 5 variance > 10: " + str(class_variance_top_5))
        else:
            print("Top 5 average not in bounds: " + str(class_average_top_5))
    else:
        print("Max < 64: " + str(class_done['Hgt'].head(8).max()))
    #print(class_done.head(30))
        

/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

Top 5 average not in bounds: 65.2


/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

Top 5 average not in bounds: 64.8
Top 5 average not in bounds: 62.6


/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

...

/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

Top 5 average not in bounds: 62.0
Top 5 average not in bounds: 64.2


/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

Top 5 average not in bounds: 63.0
Max < 64: 61
Top 5 average not in bounds: 65.6
2017


/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  class_final['Ovr_stp1'] = ((5 *class_final['Hgt'] + 1 *class_final['Stre'] + 4 *class_final['Spd'] + 2 *class_final['Jmp'] + 1 *class_final['Endu'] + 1 *class_final['Ins'] + 2 *class_final['Dnk'] + 1 *class_final['Ft'] + 1 *class_final['Fg'] + 3 *class_final['Tp'] + 7 *class_final['Oiq'] + 3 *class_final['Diq'] + 3 *class_final['Drb'] + 3 *class_final['Pss'] + 1 * class_final['Reb']) / 38.)
/var/folders/95/q06718vx3nd9m5683mchd0380000gn/T/ipykernel_2249/1641963488.py:58: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See

In [70]:

class_done['Ovr'].head(5).mean(axis=0)

68.8

In [71]:
class_done['Ovr'].head(5).var(axis=0)

9.7

In [72]:
class_done.loc[29,'Ovr']

54

In [73]:
class_done.loc[149,'Ovr']

35

In [74]:
class_done.loc[249,'Ovr']

26

In [75]:
#pd.options.display.max_rows = 999

In [76]:
test = class_done.loc[(class_done['Name'] == "Marquis Levett") & (class_done['Hgt'] == 42)]
test

Empty DataFrame
Columns: [Name, playerType, Ovr, Ovr_stp1, Hgt, Stre, Spd, Jmp, Endu, Ins, Dnk, Ft, Fg, Tp, Oiq, Diq, Drb, Pss, Reb, Hometown, HS]
Index: []

[0 rows x 21 columns]

In [77]:
def generateLoc(locations,i,name):
    keys = list(locations.keys())
    rand = random.random()
    for i in range(0,len(keys)):
        if keys[i] == rand:
            key = keys[i]
            break
        if keys[i] > rand:
            key = keys[i-1]
            break
    return(locations[key])

In [78]:
def haversine(coords1,coords2):
    lat1 = (coords1[0])*pi/180
    lat2 = (coords2[0])*pi/180
    long1 = (coords1[1])*pi/180
    long2 = (coords2[1])*pi/180
    
    latDiff = lat1-lat2
    longDiff = long1-long2
    
    hav = ((1-cos(latDiff))/2) + ((cos(lat1))*(cos(lat2))*((1-cos(longDiff))/2)) 
    return 7917.5*sqrt(asin(hav))

In [79]:
def generateHS(location,t50,t250,t1500Cities,t1500Coords,i,name, cityToCoords):
    rng = 1
    
    if i <= 250:
    
        if i <= 30:
            leaveState = random.randint(1,15)
            rng = 15
        elif i <= 90:
            leaveState = random.randint(1,20)
            rng = 20
        elif i <= 150:
            leaveState = random.randint(1,25)
            rng = 25
        else:
            leaveState = random.randint(1,30)
            rng = 30
        if type(location) == str:
            if i in internationals:
                if (i <= 150 and leaveState > 4) or (i > 150 and leaveState > 5): 
                    leaveState = 10
                else:
                    return
            else:
                city = location.split(", ")[-2]
                state = location.split(", ")[-1]
        else:
            city = location[0][0]
            state = location[0][1]
            coords = location[1]
              
        if leaveState == 10:
            random.shuffle(t50)
            random.shuffle(t50)
            random.shuffle(t50)
            return t50[0]
        
        if i <= 30:
            inStateT250 = random.randint(1,5)
            rng = 5
        elif i <= 75:
            inStateT250 = random.randint(1,7)
            rng = 7
        elif i <= 100:
            inStateT250 = random.randint(1,10)
            rng = 10
        elif i <= 150:
            inStateT250 = random.randint(1,15)
            rng = 15
        else:
            inStateT250 = random.randint(1,20)
            rng = 20
        
        if inStateT250 == 5:
            eligibleSchools = list(filter(lambda x: x[1] == state, t250))
            if len(eligibleSchools) != 0:
                random.shuffle(eligibleSchools)
                random.shuffle(eligibleSchools)
                random.shuffle(eligibleSchools)
                return eligibleSchools[0][0]
    else:
        if type(location) != str:
            city = location[0][0]
            state = location[0][1]
            coords = location[1]
        else:
            city = location.split(", ")[-2]
            state = location.split(", ")[-1]

    if city + ", " + state in t1500Cities:
        #print(city + ", " + state)
        #print("in CITY")
        eligibleSchools = t1500Cities[city + ", " + state]
        random.shuffle(eligibleSchools)
        random.shuffle(eligibleSchools)
        random.shuffle(eligibleSchools)
        return eligibleSchools[0]
    else:
        if city + ", " + state in cityToCoords:
            #print("city not Found")
            coords = cityToCoords[city + ", " + state][1]
            keys = list(t1500Coords.keys())
            keys.sort(key= lambda x: haversine(coords,(x[0],x[1])))
            eligibleSchools = t1500Coords[keys[0]]
            random.shuffle(eligibleSchools)
            random.shuffle(eligibleSchools)
            random.shuffle(eligibleSchools)
            return eligibleSchools[0]
         
    return "N/A"

In [80]:

loc = ("location_info/NCBCA Recruit Locations Generator.xlsx") 
wb = xlrd.open_workbook(loc) 
sheet = wb.sheet_by_index(1)

In [81]:
loc2 = ("location_info/High School Randomizer.xlsx")
wb2 = xlrd.open_workbook(loc2) 
topFifty = wb2.sheet_by_index(4)
topTwoFifty = wb2.sheet_by_index(5)
topFifteenHundred = wb2.sheet_by_index(6)

In [82]:
t50 = []
t250 = []
t1500Cities = {}
t1500Coords = {}

In [83]:
for i in range(1,51):
    t50.append(topFifty.cell_value(i,1))
    
t50 = 7 * t50[0:5] + 4 * t50[5:15] + 2 * t50[15:25] + t50[25:] #WEIGHTS

In [84]:
for i in range(0,449):
    if (topTwoFifty.cell_value(i,1), topTwoFifty.cell_value(i,2)) not in t250:
        t250.append((topTwoFifty.cell_value(i,1), topTwoFifty.cell_value(i,2)))
        
t250 = 5 * t250[0:25] + 3 * t250[25:50] + 2 * t250[50:100] + t250[100:] #WEIGHTS

In [85]:
for i in range(1,1501):
    city = topFifteenHundred.cell_value(i,4)
    state = topFifteenHundred.cell_value(i,2)
    HS = topFifteenHundred.cell_value(i,1)
    coords = (topFifteenHundred.cell_value(i,7),topFifteenHundred.cell_value(i,8))
    
    if city + ", " + state not in t1500Cities:
        t1500Cities[city + ", " + state] = [HS]
    else:
        t1500Cities[city + ", " + state].append(HS)
        
    if coords not in t1500Coords:
        t1500Coords[coords] = [HS]
    else:
        t1500Coords[coords].append(HS)

In [86]:
locations = {}
cityToCoords = {}
for i in range(1,19360):
    locations[sheet.cell_value(i,5)] = ((sheet.cell_value(i,1),sheet.cell_value(i,0)),((sheet.cell_value(i,6),(sheet.cell_value(i,7)))))
    cityToCoords[(sheet.cell_value(i,1) + ", " + sheet.cell_value(i,0))] = ((sheet.cell_value(i,1),sheet.cell_value(i,0)),((sheet.cell_value(i,6),(sheet.cell_value(i,7)))))

In [87]:
for index, row in class_done.iterrows():
    if index+1 not in internationals:
        location = generateLoc(locations, index+1, row['Name'])
        class_done.at[index, "Hometown"] = location[0][0] + ", " + location[0][1]
    else:
        class_done.at[index, "Hometown"] = intl[index+1]
        location = "INTERNATIONAL, LOCATION"
    #print(location)
    hs = generateHS(location, t50,t250,t1500Cities,t1500Coords,index+1,row['Name'], cityToCoords)
    
    if hs is None:
        hs = "EUROLEAGUE"
    print(location, index+1, hs)
    class_done.at[index, "HS"] = hs
class_done["Pos"] = ""

(('Des Moines', 'IA'), (41.5725, -93.6104)) 1 Sheldon (Sacramento)
(('San Angelo', 'TX'), (31.4424, -100.4503)) 2 Midland Christian (Midland)
(('Williams', 'AZ'), (35.2476, -112.1833)) 3 Cactus Shadows (Cave Creek)
(('Chicago', 'IL'), (41.8373, -87.6861)) 4 Corliss (Chicago)
(('Keller', 'TX'), (32.9337, -97.2256)) 5 Keller
(('Highland Park', 'NJ'), (40.5006, -74.4284)) 6 Rutgers Prep (Somerset)
(('Hanahan', 'SC'), (32.9303, -80.0031)) 7 Myrtle Beach
(('Warrenton', 'GA'), (33.4067, -82.6653)) 8 Hancock Central (Sparta)
(('Wauwatosa', 'WI'), (43.0616, -88.0347)) 9 Wauwatosa West (Wauwatosa)
(('Savoonga', 'AK'), (63.6803, -170.4825)) 10 Lumen Christi (Anchorage)
(('Philadelphia', 'PA'), (40.0076, -75.134)) 11 Math Civics & Sciences (Philadelphia)
(('Humble', 'TX'), (29.992, -95.2656)) 12 Atascocita (Humble)
INTERNATIONAL, LOCATION 13 Centennial (Corona)
INTERNATIONAL, LOCATION 14 EUROLEAGUE
(('Summit', 'IL'), (41.7877, -87.8146)) 15 Lyons (LaGrange)
(('Batesville', 'IN'), (39.2974, -85.21

(('Ironton', 'OH'), (38.5319, -82.6777)) 206 Blazer (Ashland)
(('Jonesboro', 'LA'), (32.2348, -92.7098)) 207 West Monroe
(('Chicago', 'IL'), (41.8373, -87.6861)) 208 Bogan (Chicago)
INTERNATIONAL, LOCATION 209 Montverde Academy (Montverde)
INTERNATIONAL, LOCATION 210 Long Island Lutheran (Brookville)
(('Bellflower', 'CA'), (33.888, -118.1271)) 211 St. John Bosco (Bellflower)
(('Chicago', 'IL'), (41.8373, -87.6861)) 212 DePaul College Prep (Chicago)
(('Chesapeake', 'VA'), (36.6778, -76.3024)) 213 Western Branch (Chesapeake)
(('Vineland', 'NJ'), (39.4652, -74.9981)) 214 Montverde Academy (Montverde)
(('Coconut Creek', 'FL'), (26.2803, -80.1842)) 215 Calvary Christian Academy (Fort Lauderdale)
(('Los Angeles', 'CA'), (34.114, -118.4068)) 216 Brentwood School (Los Angeles)
INTERNATIONAL, LOCATION 217 Etiwanda
(('Washington', 'DC'), (38.9047, -77.0163)) 218 Roosevelt (Washington)
(('Jacksonville', 'FL'), (30.3322, -81.6749)) 219 Andrew Jackson (Jacksonville)
(('Scotia', 'NE'), (41.4678, -98

(('Rockton', 'IL'), (42.45, -89.0631)) 403 Turner (Beloit)
(('Lantana', 'FL'), (26.5834, -80.0558)) 404 Park Vista (Lake Worth)
(('Hagerstown', 'MD'), (39.6401, -77.7217)) 405 Martinsburg
(('Baton Rouge', 'LA'), (30.4422, -91.1314)) 406 Madison Prep Academy (Baton Rouge)
(('Chicago', 'IL'), (41.8373, -87.6861)) 407 Simeon (Chicago)
(('West Columbia', 'SC'), (33.9948, -81.0878)) 408 Gray Collegiate Academy (West Columbia)
(('Hopewell', 'VA'), (37.2914, -77.2985)) 409 Life Christian Academy (Chester)
(('Columbus', 'OH'), (39.9859, -82.9852)) 410 Walnut Ridge (Columbus)
(('Durango', 'CO'), (37.2744, -107.8702)) 411 Cleveland (Rio Rancho)
(('Murfreesboro', 'TN'), (35.851, -86.4093)) 412 Siegel (Murfreesboro)
(('Lafayette', 'LA'), (30.2097, -92.0314)) 413 Lafayette
INTERNATIONAL, LOCATION 414 N/A
(('Du Bois', 'PA'), (41.1225, -78.7564)) 415 Bishop Guilfoyle (Altoona)
(('Madison', 'WI'), (43.0809, -89.3921)) 416 Madison La Follette (Madison)
(('Avon', 'IN'), (39.7604, -86.3916)) 417 Plainfie

In [88]:
intl

{14: 'Mississauga, Canada',
 39: 'Novi Sad, Serbia',
 20: 'Melbourne, Australia',
 36: 'Nassau, Bahamas',
 13: 'Milan, Italy',
 75: 'Antwerp, Belgium',
 72: 'Thies, Senegal',
 67: 'Duisburg, Germany',
 58: 'Melbourne, Australia',
 60: 'Saint-Marc, Haiti',
 122: 'Zagreb, Croatia',
 149: 'Jonava, Lithuania',
 137: 'Toronto, Canada',
 115: 'Paris, France',
 138: 'Bunbury, Australia',
 164: 'North Vancouver, Canada',
 185: 'Orleans, France',
 154: 'Winnipeg, Canada',
 177: 'Aksu, China',
 183: 'Middlesex Centre, Canada',
 217: 'Pikine, Senegal',
 245: 'Geelong, Australia',
 210: 'Podgorica, Montenegro',
 236: 'Bolsward, Netherlands',
 209: 'Yaounde, Cameroon',
 254: 'Glyfada, Greece',
 272: 'Saint-Denis, Reunion',
 290: 'Coronel Freitas, Brazil',
 271: 'Ibadan, Nigeria',
 285: 'Tafalla, Spain',
 338: 'Karlsruhe, Germany',
 342: 'Dublin, Ireland',
 301: 'Hong Kong, Hong Kong',
 348: 'Chatham, Canada',
 309: 'Mississauga, Canada',
 389: 'Sidon, Lebanon',
 367: 'Saint-Jean-sur-Richelieu, Cana

In [89]:
class_done.head(30)

Name      playerType  Ovr   Ovr_stp1  Hgt  Stre  Spd  Jmp  \
0      Mujo Milosevic       versatile   72  64.684211   58    63   90   82   
1       Brandon Rybak         captain   71  63.552632   63    80   90   84   
2        Jerry Wilson         slasher   69  61.921053   53    61   89   80   
3        Isaiah Green         captain   68  61.289474   46    63   74   78   
4        Stephon Kell       versatile   64  57.894737   58    60   90   89   
5         Kevin Ewing       versatile   63  57.105263   50    58   73   85   
6       Marius Ritter      triple dub   63  57.315789   55    64   63   71   
7      Cheick Diakite  athletic guard   62  56.263158   48    81   99  100   
8       LaVell Stokes         shooter   62  56.342105   45    47   70   67   
9     Anthony Douglas       versatile   61  55.921053   44    54   85   84   
10       Chris Walker  athletic guard   59  54.157895   52    71   89   89   
11    Davide Righetti   offensive big   59  54.289474   67    75   53   59   
12       Matt Woodall       versatile   59  53.710526   43    54   83   82   
13   Ambrose Jennings         derozan   57  52.052632   45    60   62   55   
14  Darryl Schintzius      triple dub   57  52.447368   51    75   70   70   
15        Gary Hansen      triple dub   57  52.789474   41    69   68   78   
16         Sean Johns       versatile   56  51.289474   51    60   81   81   
17        Jerry Camus   offensive big   56  52.026316   61    77   51   51   
18        Otis Battle         slasher   56  51.578947   33    50   65   68   
19       Evan Comeaux   offensive big   55  50.526316   72    69   44   54   
20  Vaggelis Stamatis         slasher   55  50.710526   42    57   84   77   
21      Nate Quintana         3_and_d   55  50.552632   50    73   79   80   
22      Robert Butler         slasher   55  50.921053   39    55   92   78   
23      Tyler Holland      triple dub   55  50.736842   46    67   71   74   
24        Thomas Lamb  athletic guard   55  50.684211   47    65   94   79   
25       Lucious Ford    fundamentals   55  50.657895   59    45   34   34   
26       Tez Hillsman         shooter   54  49.736842   57    36   60   59   
27      Mikhail Jadin         shooter   54  49.447368   48    43   59   63   
28       Wesley Mejia    defense only   54  50.105263   41    70   90   84   
29  Johnathan Crisman     stretch big   54  49.763158   80    58   58   60   

    Endu  Ins  ...  Fg  Tp  Oiq  Diq  Drb  Pss  Reb              Hometown  \
0     33   40  ...  76  70   61   45   73   64   54        Des Moines, IA   
1     59   52  ...  35  34   61   53   67   76   70        San Angelo, TX   
2     42   59  ...  69  55   59   44   76   56   46          Williams, AZ   
3     39   59  ...  56  73   58   60   72   64   63           Chicago, IL   
4     35   40  ...  41  36   49   43   66   65   64            Keller, TX   
5     44   43  ...  66  67   42   40   66   56   78     Highland Park, NJ   
6     29   45  ...  42  63   52   46   61   77   82           Hanahan, SC   
7     52   62  ...  52  49   31   32   61   54   58         Warrenton, GA   
8     32   45  ...  78  93   55   19   60   51   40         Wauwatosa, WI   
9     37   42  ...  73  71   41   42   51   47   75          Savoonga, AK   
10    48   54  ...  62  55   31   31   62   45   50      Philadelphia, PA   
11    33   61  ...  52  42   48   31   61   52   90            Humble, TX   
12    32   34  ...  35  37   52   42   60   63   54          Milan, Italy   
13    33   38  ...  95  23   54   40   68   60   53   Mississauga, Canada   
14    35   43  ...  37  38   48   29   60   81   46            Summit, IL   
15    31   49  ...  44  48   49   28   61   74   71        Batesville, IN   
16    30   36  ...  53  55   33   40   50   43   71        Long Beach, CA   
17    37   58  ...  65  47   44   39   58   50   62   California City, CA   
18    29   61  ...  49  42   57   33   70   53   56         Woodstock, GA   
19    31   55  ...  36  29   45   33   54   58   83  Melbo

In [90]:
def update(class_done, json):
    for player in json.get("players"):
        ratings = player["ratings"][-1];
        if ratings["season"] == year - diff and player["tid"] == tid and year - player.get("born")["year"] == age:
            name = player["firstName"] + " " + player["lastName"]
            new_rtgs = class_done.loc[(class_done['Name'] == name) & (class_done['Hgt'] == ratings["hgt"])]
            if(new_rtgs.empty):
                print(name + " could not be updated! Fix manually")
            else:
                class_done.loc[(class_done['Name'] == name) & (class_done['Hgt'] == ratings["hgt"]), "pos"] = calcPos(ratings)
                ratings["stre"] = int(new_rtgs["Stre"].iloc[0])
                ratings["spd"] = int(new_rtgs["Spd"].iloc[0])
                ratings["jmp"] = int(new_rtgs["Jmp"].iloc[0])
                ratings["endu"] = int(new_rtgs["Endu"].iloc[0])
                ratings["ins"] = int(new_rtgs["Ins"].iloc[0])
                ratings["dnk"] = int(new_rtgs["Dnk"].iloc[0])
                ratings["ft"] = int(new_rtgs["Ft"].iloc[0])
                ratings["fg"] = int(new_rtgs["Fg"].iloc[0])
                ratings["tp"] = int(new_rtgs["Tp"].iloc[0])
                ratings["oiq"] = int(new_rtgs["Oiq"].iloc[0])
                ratings["diq"] = int(new_rtgs["Diq"].iloc[0])
                ratings["drb"] = int(new_rtgs["Drb"].iloc[0])
                ratings["pss"] = int(new_rtgs["Pss"].iloc[0])
                ratings["reb"] = int(new_rtgs["Reb"].iloc[0])
                ratings["ovr"] = int(new_rtgs["Ovr"].iloc[0])
                player["city"] = str(new_rtgs["Hometown"].iloc[0].split(", ")[0])
                player["state"] = str(new_rtgs["Hometown"].iloc[0].split(", ")[1])
                player["college"] = new_rtgs["HS"].iloc[0]
                if len(str(new_rtgs["Hometown"].iloc[0].split(", ")[1])) > 2:
                    country = str(new_rtgs["Hometown"].iloc[0].split(", ")[1]).split(" (IR)")[0]
                    print(country)
                    player["state"] = country
                    player["born"]["loc"] = country
                    new_name = getName(country)
                    if new_name != None:
                        player["firstName"] = new_name[0]
                        player["lastName"] = new_name[1]
                        print(class_done.loc[(class_done['Name'] == name) & (class_done['Hgt'] == ratings["hgt"]), 'Name'])
                        class_done.loc[(class_done['Name'] == name) & (class_done['Hgt'] == ratings["hgt"]), 'Name'] = new_name[0] + " " + new_name[1]
                ratings["skills"] = []
                for badge in ['3', 'A', 'B', 'Di', 'Dp', 'Po', 'Ps', 'R']:
                    info = getAtts(badge)
                    atts = info[0]
                    weights = info[1]
                    cutoff = info[2]
                    rtgs = []
                    for att in atts:
                        rtgs.append(int(new_rtgs[att].iloc[0]))
                    if getComposite(rtgs, weights) > cutoff:
                        ratings["skills"].append(badge)

In [91]:
update(class_done, obj)

England
467    Michael Rimmer
Name: Name, dtype: object
Canada
456    DeAngelo Rambis
Name: Name, dtype: object
Finland
413    Kiwi Tomko
Name: Name, dtype: object
China
176    Greg Taylor
Name: Name, dtype: object
Nigeria
270    John Poston
Name: Name, dtype: object
Canada
488    Zvonimir Jankovic
Name: Name, dtype: object
Canada
347    Jamar Harris
Name: Name, dtype: object
Montenegro
209    Prince Sanford
Name: Name, dtype: object
Canada
182    Jasmin Asceric
Name: Name, dtype: object
Croatia
121    Tony Calixte
Name: Name, dtype: object
Belgium
74    Anton Stepanenkov
Name: Name, dtype: object
Canada
153    Pieter Van Kempen
Name: Name, dtype: object
Spain
284    Angel Rivera
Name: Name, dtype: object
Germany
66    Chris Thomas
Name: Name, dtype: object
Belgium
428    Justin Burton
Name: Name, dtype: object
Australia
244    Will Law
Name: Name, dtype: object
Haiti
59    David Wallace
Name: Name, dtype: object
France
184    Sam Hinds
Name: Name, dtype: object
Canada
506    Markhuri 

In [92]:
class_done.head(30)

Name      playerType  Ovr   Ovr_stp1  Hgt  Stre  Spd  Jmp  \
0      Mujo Milosevic       versatile   72  64.684211   58    63   90   82   
1       Brandon Rybak         captain   71  63.552632   63    80   90   84   
2        Jerry Wilson         slasher   69  61.921053   53    61   89   80   
3        Isaiah Green         captain   68  61.289474   46    63   74   78   
4        Stephon Kell       versatile   64  57.894737   58    60   90   89   
5         Kevin Ewing       versatile   63  57.105263   50    58   73   85   
6       Marius Ritter      triple dub   63  57.315789   55    64   63   71   
7      Cheick Diakite  athletic guard   62  56.263158   48    81   99  100   
8       LaVell Stokes         shooter   62  56.342105   45    47   70   67   
9     Anthony Douglas       versatile   61  55.921053   44    54   85   84   
10       Chris Walker  athletic guard   59  54.157895   52    71   89   89   
11    Davide Righetti   offensive big   59  54.289474   67    75   53   59   
12     Stefano Caruso       versatile   59  53.710526   43    54   83   82   
13    Douglas Gervais         derozan   57  52.052632   45    60   62   55   
14  Darryl Schintzius      triple dub   57  52.447368   51    75   70   70   
15        Gary Hansen      triple dub   57  52.789474   41    69   68   78   
16         Sean Johns       versatile   56  51.289474   51    60   81   81   
17        Jerry Camus   offensive big   56  52.026316   61    77   51   51   
18        Otis Battle         slasher   56  51.578947   33    50   65   68   
19  Brendan Magliozzi   offensive big   55  50.526316   72    69   44   54   
20  Vaggelis Stamatis         slasher   55  50.710526   42    57   84   77   
21      Nate Quintana         3_and_d   55  50.552632   50    73   79   80   
22      Robert Butler         slasher   55  50.921053   39    55   92   78   
23      Tyler Holland      triple dub   55  50.736842   46    67   71   74   
24        Thomas Lamb  athletic guard   55  50.684211   47    65   94   79   
25       Lucious Ford    fundamentals   55  50.657895   59    45   34   34   
26       Tez Hillsman         shooter   54  49.736842   57    36   60   59   
27      Mikhail Jadin         shooter   54  49.447368   48    43   59   63   
28       Wesley Mejia    defense only   54  50.105263   41    70   90   84   
29  Johnathan Crisman     stretch big   54  49.763158   80    58   58   60   

    Endu  Ins  ...  Tp  Oiq  Diq  Drb  Pss  Reb              Hometown  \
0     33   40  ...  70   61   45   73   64   54        Des Moines, IA   
1     59   52  ...  34   61   53   67   76   70        San Angelo, TX   
2     42   59  ...  55   59   44   76   56   46          Williams, AZ   
3     39   59  ...  73   58   60   72   64   63           Chicago, IL   
4     35   40  ...  36   49   43   66   65   64            Keller, TX   
5     44   43  ...  67   42   40   66   56   78     Highland Park, NJ   
6     29   45  ...  63   52   46   61   77   82           Hanahan, SC   
7     52   62  ...  49   31   32   61   54   58         Warrenton, GA   
8     32   45  ...  93   55   19   60   51   40         Wauwatosa, WI   
9     37   42  ...  71   41   42   51   47   75          Savoonga, AK   
10    48   54  ...  55   31   31   62   45   50      Philadelphia, PA   
11    33   61  ...  42   48   31   61   52   90            Humble, TX   
12    32   34  ...  37   52   42   60   63   54          Milan, Italy   
13    33   38  ...  23   54   40   68   60   53   Mississauga, Canada   
14    35   43  ...  38   48   29   60   81   46            Summit, IL   
15    31   49  ...  48   49   28   61   74   71        Batesville, IN   
16    30   36  ...  55   33   40   50   43   71        Long Beach, CA   
17    37   58  ...  47   44   39   58   50   62   California City, CA   
18    29   61  ...  42   57   33   70   53   56         Woodstock, GA   
19    31   55  ...  29   45   33   54   58   83  Melbourne, Australia   
20    29   53  ...  45   40   34   56   40   41          Fort Lee

In [93]:
writeJSON(fileName, obj)

In [94]:
class_done.iloc[[x-1 for x in internationals], class_done.columns.get_loc("Hometown")] = class_done.iloc[[x-1 for x in internationals], class_done.columns.get_loc("Hometown")].astype(str) + " (IR)"

In [95]:
class_done.to_csv(str(year+years_in_future)+".csv")

In [96]:
print(generateHS("Oakland, OK", t50,t250,t1500Cities,t1500Coords,1,"boi", cityToCoords))

Prosper
